In [1]:
import pandas as pd
import nltk
# nltk.download('all')
import re
import numpy as np
import collections
import sklearn as sk
import string
from nltk.corpus import stopwords
from wordcloud import WordCloud, STOPWORDS
stopwords = set(STOPWORDS)

In [2]:
# df = pd.read_csv("../B_Data_Cleaning/synthetic_reviews_all.csv")
df = pd.read_csv("../B_Data_Cleaning/synthetic_reviews_all_trial.csv")
df["Review"] = df["Review"].astype("str")
df

Review  \
0      ультра exploiters swaying bem sinced footright...   
1      punkedup left nonimmersive sold representing b...   
2      aestethic slums господи iextend тяжелее weirdn...   
3      chemicals exmple carpenter gunz homosexual dep...   
4       uneventful bugsaways whispered mojave cutremoved   
...                                                  ...   
16570  nonimmersive bloggers ubthis animes cone intri...   
16571  roleplayb parkor seeking funneling expanded ch...   
16572  insignificant holotape adultstuff ssh aprimora...   
16573  intensely thinkmaybe antenna iceskate okeish a...   
16574  uprosu spoilerhighly jk awesome toolplaystyle ...   

       Recommended or Not Recommended  
0                                True  
1                                True  
2                                True  
3                                True  
4                                True  
...                               ...  
16570                           False  
16571                           False  
16572                           False  
16573                           False  
16574                           False  

[16575 rows x 2 columns]

In [3]:
# Checking the length of all the reviews
(df["Review"]=='').value_counts()

False    16575
Name: Review, dtype: int64

In [4]:
# make a set_column to count the number of words in each review
df["set_column"] = df["Review"].apply(lambda x: set(x.split()))
df

Review  \
0      ультра exploiters swaying bem sinced footright...   
1      punkedup left nonimmersive sold representing b...   
2      aestethic slums господи iextend тяжелее weirdn...   
3      chemicals exmple carpenter gunz homosexual dep...   
4       uneventful bugsaways whispered mojave cutremoved   
...                                                  ...   
16570  nonimmersive bloggers ubthis animes cone intri...   
16571  roleplayb parkor seeking funneling expanded ch...   
16572  insignificant holotape adultstuff ssh aprimora...   
16573  intensely thinkmaybe antenna iceskate okeish a...   
16574  uprosu spoilerhighly jk awesome toolplaystyle ...   

       Recommended or Not Recommended  \
0                                True   
1                                True   
2                                True   
3                                True   
4                                True   
...                               ...   
16570                           False   
16571                           False   
16572                           False   
16573                           False   
16574                           False   

                                              set_column  
0      {footright, lequelles, selfish, alix, plants, ...  
1      {insight, beatifuk, oneline, metalheadrockerbo...  
2      {canon, tournament, escada, esperaria, nothing...  
3      {deceptively, chemicals, handcraft, crafty, ba...  
4      {cutremoved, mojave, uneventful, whispered, bu...  
...                                                  ...  
16570  {selection, dialogueinteraction, relabeled, де...  
16571  {stylistic, offsets, gehabt, hellgate, badly, ...  
16572  {blew, bimproved, toasters, glorious, gameread...  
16573  {discoveryquest, pubg, ia, tipstutorialsmenus,...  
16574  {entomologists, cardiacarrestinducingly, soooo...  

[16575 rows x 3 columns]

In [5]:
# split the data into train and test
train, test = sk.model_selection.train_test_split(df, test_size=0.33, random_state=42)

In [6]:
# Dividing dataset into recommended and not recommended
df_recom = train.loc[train["Recommended or Not Recommended"] == True,:]
df_recom = df_recom.reset_index(drop=True)

df_not_recom = train.loc[train["Recommended or Not Recommended"] == False,:]
df_not_recom = df_not_recom.reset_index(drop=True)

In [7]:
# This is to make the set dictionary
# count how many times each word appears in the reviews
bow_recom_temp = collections.Counter([y for x in df_recom.set_column for y in x])
bow_not_recom_temp = collections.Counter([y for x in df_not_recom.set_column for y in x])

bow_recom_set = dict(bow_recom_temp)
bow_not_recom_set = dict(bow_not_recom_temp)

for key in bow_recom_set:
    if key not in bow_not_recom_set:
        bow_not_recom_set[key] = 0
        pass
    else:
        pass

for key in bow_not_recom_set:
    if key not in bow_recom_set:
        bow_recom_set[key] = 0
        pass
    else:
        pass

for key in bow_recom_set:
    bow_recom_set[key] += 1

for key in bow_not_recom_set:
    bow_not_recom_set[key] += 1


In [8]:
# This is to make the list dictionary
# count how many times each word appears in the reviews
bow_recom = collections.Counter([y for x in df_recom.Review for y in x.split()])
bow_not_recom = collections.Counter([y for x in df_not_recom.Review for y in x.split()])

bow_recom_dict = dict(bow_recom)
bow_not_recom_dict = dict(bow_not_recom)

for key in bow_recom_dict:
    if key not in bow_not_recom_dict:
        bow_not_recom_dict[key] = 0
        pass
    else:
        pass

for key in bow_not_recom_dict:
    if key not in bow_recom_dict:
        bow_recom_dict[key] = 0
        pass
    else:
        pass

for key in bow_recom_dict:
    bow_recom_dict[key] += 1

for key in bow_not_recom_dict:
    bow_not_recom_dict[key] += 1
    

In [9]:
bow_recom_sum_vals = sum(bow_recom_dict.values())
bow_not_recom_sum_vals = sum(bow_not_recom_dict.values())

for i in bow_recom_dict:

    bow_recom_dict[i] /= bow_recom_sum_vals

for i in bow_not_recom_dict:

    bow_not_recom_dict[i] /= bow_not_recom_sum_vals

In [10]:
assert len(bow_recom_dict) == len(bow_not_recom_dict)
assert len(bow_recom_set) == len(bow_not_recom_set)

In [11]:
test.drop(columns=["set_column"], inplace=True)

In [12]:
def define_sentiment_all(element,test1=False, test2=False):

    """This function takes a review and returns the label for that review"""

    full_shape = df.shape[0]
    positive_review_probabiliy = len(df_recom)/full_shape
    negative_review_probabiliy = len(df_not_recom)/full_shape
    
    df_choices_positive = [positive_review_probabiliy, bow_recom_set, bow_recom_dict, df_recom]
    df_choices_negative = [negative_review_probabiliy ,bow_not_recom_set, bow_not_recom_dict, df_not_recom]

    def classifier(element, your_class = 'positive'):
        flag = {}
        flag_count = 0
        if your_class == 'positive':
            df_choices = df_choices_positive
        else:
            df_choices = df_choices_negative
        prob_of_class = df_choices[0]/full_shape
        score = 1 * prob_of_class
        score = float(format(score, '.12f'))
        # score = 0.1
        for i in element.split():
            if i not in df_choices[2].keys():
                pass
            else:
                prob_word_given_class = (df_choices[2])[i]
                prob_word_given_class = float(format(prob_word_given_class, '.12f'))
                # Almost the same value, given our spin on this application. 
                # Normally, this term frequency would be calculated differently across the positive and negative documents
                # but we are only looking at the reviews as the documents themselves to determine a word's relevance in the positive
                # or negative corpus. 
                tf = np.log(prob_word_given_class)
                # tf = float(format(tf, '.12f'))
                # tf = abs(np.log(prob_word_given_class))
                # The IDF is the number of reviews / the number of reviews that contain the word in that given corpus
                # idf = abs(np.log(df_choices[3].shape[0]/(df_choices[1])[i]))
                idf = np.log(df_choices[3].shape[0]/(df_choices[1])[i])
                # idf = float(format(idf, '.12f'))
                score *= prob_word_given_class*tf*idf
                # score *= prob_word_given_class*idf
                # score *= prob_word_given_class*tf
                # score *= prob_word_given_class

                if score < 0:
                    flag[flag_count] = (score, your_class)
                    print(flag_count,i)
                    flag_count += 1


        return score
    positive_score = classifier(element, 'positive')
    negative_score = classifier(element, 'negative')
    if positive_score > negative_score:
        return True
    elif positive_score == negative_score:
        # Choosing an arbitrary value, because we assume that a review with one or few words of little substance
        # is implied to be negative, as is usual with netizens. 
        return False
    else:
        return False

In [13]:
def define_sentiment_idf(element,test1=False, test2=False):

    """This function takes a review and returns the label for that review"""

    full_shape = df.shape[0]
    positive_review_probabiliy = len(df_recom)/full_shape
    negative_review_probabiliy = len(df_not_recom)/full_shape
    
    df_choices_positive = [positive_review_probabiliy, bow_recom_set, bow_recom_dict, df_recom]
    df_choices_negative = [negative_review_probabiliy ,bow_not_recom_set, bow_not_recom_dict, df_not_recom]

    def classifier(element, your_class = 'positive'):
        flag = {}
        flag_count = 0
        if your_class == 'positive':
            df_choices = df_choices_positive
        else:
            df_choices = df_choices_negative
        prob_of_class = df_choices[0]/full_shape
        score = 1 * prob_of_class
        score = float(format(score, '.12f'))
        # score = 0.1
        for i in element.split():
            if i not in df_choices[2].keys():
                pass
            else:
                prob_word_given_class = (df_choices[2])[i]
                prob_word_given_class = float(format(prob_word_given_class, '.12f'))
                # Almost the same value, given our spin on this application. 
                # Normally, this term frequency would be calculated differently across the positive and negative documents
                # but we are only looking at the reviews as the documents themselves to determine a word's relevance in the positive
                # or negative corpus. 
                tf = np.log(prob_word_given_class)
                # tf = float(format(tf, '.12f'))
                # tf = abs(np.log(prob_word_given_class))
                # The IDF is the number of reviews / the number of reviews that contain the word in that given corpus
                # idf = abs(np.log(df_choices[3].shape[0]/(df_choices[1])[i]))
                idf = np.log(df_choices[3].shape[0]/(df_choices[1])[i])
                # idf = float(format(idf, '.12f'))
                # score *= prob_word_given_class*tf*idf
                score *= prob_word_given_class*idf
                # score *= prob_word_given_class*tf
                # score *= prob_word_given_class

                if score < 0:
                    flag[flag_count] = (score, your_class)
                    print(flag_count,i)
                    flag_count += 1


        return score
    positive_score = classifier(element, 'positive')
    negative_score = classifier(element, 'negative')
    if positive_score > negative_score:
        return True
    elif positive_score == negative_score:
        # Choosing an arbitrary value, because we assume that a review with one or few words of little substance
        # is implied to be negative, as is usual with netizens. 
        return False
    else:
        return False

In [14]:
def define_sentiment_tf(element,test1=False, test2=False):

    """This function takes a review and returns the label for that review"""

    full_shape = df.shape[0]
    positive_review_probabiliy = len(df_recom)/full_shape
    negative_review_probabiliy = len(df_not_recom)/full_shape
    
    df_choices_positive = [positive_review_probabiliy, bow_recom_set, bow_recom_dict, df_recom]
    df_choices_negative = [negative_review_probabiliy ,bow_not_recom_set, bow_not_recom_dict, df_not_recom]

    def classifier(element, your_class = 'positive'):
        flag = {}
        flag_count = 0
        if your_class == 'positive':
            df_choices = df_choices_positive
        else:
            df_choices = df_choices_negative
        prob_of_class = df_choices[0]/full_shape
        score = 1 * prob_of_class
        score = float(format(score, '.12f'))
        # score = 0.1
        for i in element.split():
            if i not in df_choices[2].keys():
                pass
            else:
                prob_word_given_class = (df_choices[2])[i]
                prob_word_given_class = float(format(prob_word_given_class, '.12f'))
                # Almost the same value, given our spin on this application. 
                # Normally, this term frequency would be calculated differently across the positive and negative documents
                # but we are only looking at the reviews as the documents themselves to determine a word's relevance in the positive
                # or negative corpus. 
                tf = np.log(prob_word_given_class)
                # tf = float(format(tf, '.12f'))
                # tf = abs(np.log(prob_word_given_class))
                # The IDF is the number of reviews / the number of reviews that contain the word in that given corpus
                # idf = abs(np.log(df_choices[3].shape[0]/(df_choices[1])[i]))
                idf = np.log(df_choices[3].shape[0]/(df_choices[1])[i])
                # idf = float(format(idf, '.12f'))
                # score *= prob_word_given_class*tf*idf
                # score *= prob_word_given_class*idf
                score *= prob_word_given_class*tf
                # score *= prob_word_given_class

                if score < 0:
                    flag[flag_count] = (score, your_class)
                    print(flag_count,i)
                    flag_count += 1


        return score
    positive_score = classifier(element, 'positive')
    negative_score = classifier(element, 'negative')
    if positive_score > negative_score:
        return True
    elif positive_score == negative_score:
        # Choosing an arbitrary value, because we assume that a review with one or few words of little substance
        # is implied to be negative, as is usual with netizens. 
        return False
    else:
        return False

In [15]:
def define_sentiment_freq(element,test1=False, test2=False):

    """This function takes a review and returns the label for that review"""

    full_shape = df.shape[0]
    positive_review_probabiliy = len(df_recom)/full_shape
    negative_review_probabiliy = len(df_not_recom)/full_shape
    
    df_choices_positive = [positive_review_probabiliy, bow_recom_set, bow_recom_dict, df_recom]
    df_choices_negative = [negative_review_probabiliy ,bow_not_recom_set, bow_not_recom_dict, df_not_recom]

    def classifier(element, your_class = 'positive'):
        flag = {}
        flag_count = 0
        if your_class == 'positive':
            df_choices = df_choices_positive
        else:
            df_choices = df_choices_negative
        prob_of_class = df_choices[0]/full_shape
        score = 1 * prob_of_class
        score = float(format(score, '.12f'))
        # score = 0.1
        for i in element.split():
            if i not in df_choices[2].keys():
                pass
            else:
                prob_word_given_class = (df_choices[2])[i]
                prob_word_given_class = float(format(prob_word_given_class, '.12f'))
                # Almost the same value, given our spin on this application. 
                # Normally, this term frequency would be calculated differently across the positive and negative documents
                # but we are only looking at the reviews as the documents themselves to determine a word's relevance in the positive
                # or negative corpus. 
                tf = np.log(prob_word_given_class)
                # tf = float(format(tf, '.12f'))
                # tf = abs(np.log(prob_word_given_class))
                # The IDF is the number of reviews / the number of reviews that contain the word in that given corpus
                # idf = abs(np.log(df_choices[3].shape[0]/(df_choices[1])[i]))
                idf = np.log(df_choices[3].shape[0]/(df_choices[1])[i])
                # idf = float(format(idf, '.12f'))
                # score *= prob_word_given_class*tf*idf
                # score *= prob_word_given_class*idf
                # score *= prob_word_given_class*tf
                score *= prob_word_given_class

                if score < 0:
                    flag[flag_count] = (score, your_class)
                    print(flag_count,i)
                    flag_count += 1


        return score
    positive_score = classifier(element, 'positive')
    negative_score = classifier(element, 'negative')
    if positive_score > negative_score:
        return True
    elif positive_score == negative_score:
        # Choosing an arbitrary value, because we assume that a review with one or few words of little substance
        # is implied to be negative, as is usual with netizens. 
        return False
    else:
        return False

In [16]:
test["score_all"] = test.Review.apply(define_sentiment_all)
test["score_tf"] = test.Review.apply(define_sentiment_tf)
test["score_idf"] = test.Review.apply(define_sentiment_idf)
test["score_freq"] = test.Review.apply(define_sentiment_freq)

0 aboard
1 graphicphysics
2 shadiness
3 bugsmost
4 无论是对话系统perk系统还是超梦都服务于它
5 bfv
6 malfunctions
7 slaughtering
8 neckbeards
9 bugslocations
10 cutcontent
11 robux
12 poppint
13 зарабатывая
14 scummy
15 pinpoint
16 spoilerand
17 conversational
18 warn
19 payment
20 loadouts
21 suspend
22 𝕠𝕣𝕘𝕒𝕤𝕞
23 lvls
24 httpsyoutubeclapuawxq
25 incinerating
26 burned
27 environs
28 graft
29 forwarded
30 хотели
31 sticking
32 yerleri
33 passages
34 attracting
35 remapped
36 beshi
37 pledge
38 horseshit
39 extremelypowerful
40 dodgeforward
41 fresh
42 prokekt
43 tweaks
44 bırakıldık
45 бы
46 track
47 comlpex
48 wormsexplodesemit
49 shaved
50 axes
51 moaners
52 funand
53 nukem
54 everytimeafter
55 januaryfebruary
0 aboard
1 graphicphysics
2 shadiness
3 bugsmost
4 无论是对话系统perk系统还是超梦都服务于它
5 bfv
6 malfunctions
7 slaughtering
8 neckbeards
9 bugslocations
10 cutcontent
11 robux
12 poppint
13 зарабатывая
14 scummy
15 pinpoint
16 spoilerand
17 conversational
18 warn
19 payment
20 loadouts
21 suspend
22 𝕠𝕣𝕘𝕒𝕤𝕞
23 

In [17]:
print(f"This is our accuracy for (unbalanced) synthetic data when we use all the formula: {(sum(test['Recommended or Not Recommended'] == test['score_all'])/test.shape[0])*100:.2f}%")
print(f"This is our accuracy for (unbalanced) synthetic data when we use only frequency and TF: {(sum(test['Recommended or Not Recommended'] == test['score_tf'])/test.shape[0])*100:.2f}%")
print(f"This is our accuracy for (unbalanced) synthetic data when we use only frequency and IDF: {(sum(test['Recommended or Not Recommended'] == test['score_idf'])/test.shape[0])*100:.2f}%")
print(f"This is our accuracy for (unbalanced) synthetic data when we use only frequency: {(sum(test['Recommended or Not Recommended'] == test['score_freq'])/test.shape[0])*100:.2f}%")

This is our accuracy for (unbalanced) synthetic data when we use all the formula: 46.73%
This is our accuracy for (unbalanced) synthetic data when we use only frequency and TF: 47.15%
This is our accuracy for (unbalanced) synthetic data when we use only frequency and IDF: 59.89%
This is our accuracy for (unbalanced) synthetic data when we use only frequency: 54.94%


In [18]:
# Generate a confusion matrix
from sklearn.metrics import confusion_matrix
confusion_matrix(test['Recommended or Not Recommended'], test['score_all'])
# Generate a classification report
from sklearn.metrics import classification_report
print(classification_report(test['Recommended or Not Recommended'], test['score_all']))


              precision    recall  f1-score   support

       False       0.33      0.61      0.43      1805
        True       0.67      0.40      0.50      3665

    accuracy                           0.47      5470
   macro avg       0.50      0.50      0.46      5470
weighted avg       0.56      0.47      0.48      5470



In [19]:
# Generate a confusion matrix
from sklearn.metrics import confusion_matrix
confusion_matrix(test['Recommended or Not Recommended'], test['score_tf'])
# Generate a classification report
from sklearn.metrics import classification_report
print(classification_report(test['Recommended or Not Recommended'], test['score_tf']))


              precision    recall  f1-score   support

       False       0.34      0.64      0.45      1805
        True       0.69      0.39      0.49      3665

    accuracy                           0.47      5470
   macro avg       0.51      0.52      0.47      5470
weighted avg       0.57      0.47      0.48      5470



In [20]:
# Generate a confusion matrix
from sklearn.metrics import confusion_matrix
confusion_matrix(test['Recommended or Not Recommended'], test['score_idf'])
# Generate a classification report
from sklearn.metrics import classification_report
print(classification_report(test['Recommended or Not Recommended'], test['score_idf']))


              precision    recall  f1-score   support

       False       0.38      0.35      0.36      1805
        True       0.69      0.72      0.71      3665

    accuracy                           0.60      5470
   macro avg       0.54      0.54      0.54      5470
weighted avg       0.59      0.60      0.59      5470



In [21]:
# Generate a confusion matrix
from sklearn.metrics import confusion_matrix
confusion_matrix(test['Recommended or Not Recommended'], test['score_freq'])
# Generate a classification report
from sklearn.metrics import classification_report
print(classification_report(test['Recommended or Not Recommended'], test['score_freq']))


              precision    recall  f1-score   support

       False       0.37      0.50      0.42      1805
        True       0.70      0.57      0.63      3665

    accuracy                           0.55      5470
   macro avg       0.53      0.54      0.53      5470
weighted avg       0.59      0.55      0.56      5470



Bad pipe message: %s [b'H\xdd\x1bYL:\xf5dkk\xeeW\xfe\x0c\xcaMv\xdc [2\x87\xd6q\xfd\xec=\xbb<tw\x18\xcc\xbcEE\x05z8\xb2!\x7f\x8em\xaaG\x91z\x99*9\x00\x08\x13\x02\x13\x03\x13\x01\x00\xff\x01\x00\x00\x8f\x00\x00\x00\x0e\x00\x0c\x00\x00\t127.0.0.1\x00\x0b\x00\x04\x03\x00\x01\x02\x00\n\x00\x0c\x00\n\x00\x1d\x00\x17\x00\x1e\x00\x19\x00\x18\x00#\x00\x00\x00\x16\x00\x00\x00\x17\x00\x00\x00\r\x00\x1e\x00\x1c\x04\x03\x05\x03\x06']
Bad pipe message: %s [b'\x07\x08']
Bad pipe message: %s [b'\xdf\xa2\x8d`\xb7\x81\x0e\xe9\xb8\x0c#\xa8\x1d\xdd\xb2+\x8b\xb8 \xe5\xc1\x89\x81j\xf0w]\xc0G\x0cc\x85d\xf6\xdb\x98mAj\x1f\x13Q\xe8g\x036\xd8\xf4\xf7\xdb1\x00\x08\x13\x02\x13\x03\x13\x01\x00\xff\x01\x00\x00\x8f\x00\x00\x00\x0e\x00\x0c\x00\x00\t1']
Bad pipe message: %s [b'\t\x08\n\x08\x0b\x08\x04']
Bad pipe message: %s [b'.0.0.1\x00\x0b\x00\x04\x03\x00\x01\x02\x00\n\x00\x0c\x00\n\x00\x1d\x00\x17\x00\x1e\x00\x19\x00\x18\x00#\x00\x00\x00\x16\x00\x00\x00\x17\x00\x00\x00\r\x00\x1e\x00\x1c\x04', b'\x03\x06', b'\x07\x0